

# ハイパーパラメータを手動で指定する

初期学習率の値やリーフ数など、最初に試すべきハイパーパラメータのセットが具体的に決まっている場合もあります。
また、Optunaがより良いハイパーパラメータセットを見つける前に、これらのセットを既に試している場合もあります。

Optunaではこのようなケースに対応するため、以下の2つのAPIを提供しています：

1. これらのハイパーパラメータセットをOptunaに渡し、評価させる - :func:`~optuna.study.Study.enqueue_trial`
2. これらのセットの結果を完了した ``Trial`` として追加する - :func:`~optuna.study.Study.add_trial`


## 最初のシナリオ：Optunaにハイパーパラメータを評価させる

このシナリオでは、既製のハイパーパラメータセットは持っているものの、まだ評価しておらず、
Optunaを使ってより良いハイパーパラメータセットを見つけたいとします。

Optunaには :func:`optuna.study.Study.enqueue_trial` という機能があり、
この機能を使えば、Optunaにこれらのハイパーパラメータセットを渡して評価させることができます。

このセクションでは、 [LightGBM](https://lightgbm.readthedocs.io/en/stable/)_ を使った
このAPIの使用方法を説明します。


In [ ]:
import lightgbm as lgb
import numpy as np
import sklearn.datasets
import sklearn.metrics
from sklearn.model_selection import train_test_split

import optuna

目的関数を定義します。



In [ ]:
def objective(trial):
    data, target = sklearn.datasets.load_breast_cancer(return_X_y=True)
    train_x, valid_x, train_y, valid_y = train_test_split(data, target, test_size=0.25)
    dtrain = lgb.Dataset(train_x, label=train_y)
    dvalid = lgb.Dataset(valid_x, label=valid_y)

    param = {
        "objective": "binary",
        "metric": "auc",
        "verbosity": -1,
        "boosting_type": "gbdt",
        "bagging_fraction": min(trial.suggest_float("bagging_fraction", 0.4, 1.0 + 1e-12), 1),
        "bagging_freq": trial.suggest_int("bagging_freq", 0, 7),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
    }

    gbm = lgb.train(param, dtrain, valid_sets=[dvalid])

    preds = gbm.predict(valid_x)
    pred_labels = np.rint(preds)
    accuracy = sklearn.metrics.accuracy_score(valid_y, pred_labels)
    return accuracy

次に、ハイパーパラメータ最適化のための ``Study`` を作成します。



In [ ]:
study = optuna.create_study(direction="maximize", pruner=optuna.pruners.MedianPruner())

ここでは、 ``"bagging_fraction"`` の値を大きくしたセットとデフォルト値のセットを
Optunaに評価させます。



In [ ]:
study.enqueue_trial(
    {
        "bagging_fraction": 1.0,
        "bagging_freq": 0,
        "min_child_samples": 20,
    }
)

study.enqueue_trial(
    {
        "bagging_fraction": 0.75,
        "bagging_freq": 5,
        "min_child_samples": 20,
    }
)

import logging
import sys

# Optunaの動作を確認できるように、stdoutのストリームハンドラを追加します。
optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study.optimize(objective, n_trials=100, timeout=600)


## 第2のシナリオ: 既に評価済みのハイパーパラメータをOptunaに活用する

このシナリオでは、事前に設定したハイパーパラメータセットがあり、
既に評価済みだが結果が思わしくないため、Optunaの活用を検討する場合を考えます。

Optunaには :func:`optuna.study.Study.add_trial` という機能があり、
これらの結果をOptunaに登録することで、Optunaがそれらを考慮したハイパーパラメータのサンプリングを行います。

このセクションでは、 ``objective`` は第1のシナリオと同じです。



In [ ]:
study = optuna.create_study(direction="maximize", pruner=optuna.pruners.MedianPruner())
study.add_trial(
    optuna.trial.create_trial(
        params={
            "bagging_fraction": 1.0,
            "bagging_freq": 0,
            "min_child_samples": 20,
        },
        distributions={
            "bagging_fraction": optuna.distributions.FloatDistribution(0.4, 1.0 + 1e-12),
            "bagging_freq": optuna.distributions.IntDistribution(0, 7),
            "min_child_samples": optuna.distributions.IntDistribution(5, 100),
        },
        value=0.94,
    )
)
study.add_trial(
    optuna.trial.create_trial(
        params={
            "bagging_fraction": 0.75,
            "bagging_freq": 5,
            "min_child_samples": 20,
        },
        distributions={
            "bagging_fraction": optuna.distributions.FloatDistribution(0.4, 1.0 + 1e-12),
            "bagging_freq": optuna.distributions.IntDistribution(0, 7),
            "min_child_samples": optuna.distributions.IntDistribution(5, 100),
        },
        value=0.95,
    )
)
study.optimize(objective, n_trials=100, timeout=600)